# Assignment 1 

Elinor Funk, Leland Whitlock, Marlo Anzarut 

github: https://github.com/elinorfunk/compsoc_assignment1

#### Group Collaborations:
Elinor: <br>
Leland: <br>
Marlo: <br>


### Part 1

In [3]:
import requests
import pandas as pd
from bs4 import BeautifulSoup
import os 

C:\Users\whitl\AppData\Local\Temp\ipykernel_1740\2000793289.py:2: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd


In [3]:
page = requests.get('https://ic2s2-2023.org/program')
bs = BeautifulSoup(page.content)

# all names on the page are in italics
italics = bs.find_all('i')
name_list = []
for i in italics:
    names = i.get_text()
    # remove chair: from names
    clean_names = names.replace("Chair:", "")
    name_list += clean_names.split(', ')

In [4]:
# cleaning to make sure all names are in the same format
for i in range(len(name_list)):
    name_list[i] = name_list[i].strip()
    name_list[i] = name_list[i].lower()

In [5]:
# remove duplicate names
name_df = pd.DataFrame(name_list, columns=['names'])
no_dupes = name_df.drop_duplicates(keep='first', ignore_index=True)

In [6]:
no_dupes.to_csv("data/names.csv")

### Part 2 - Ready Made vs Custom Made Data 

1. Advantages with custom-made data are that you can control the sample: meaning that you can make sure that the participants in the experiment are mixed in gender, age, etc. You can also customize the specific questions that you want answered. However, there are disadvantages with experiments like this. For example, maybe only a subset of individuals choose to answer surveys, which can bias the data. In addition, it is costly to arrange experiments or surveys. 

An advantage with ready-made data is that you can easily get a large sample without it being as costly as arranging an experiment. As well, you can capture real world behavior, since the participants are not aware that their data will be tracked. A disadvantage is that the sample of people might be biased, it might only be a certain type of people that uses this fitness tracking app. 

2. As mentioned in the lecture videos, the results of the second study might be biased since you are more likely to be friends with people acting in a similar manner as you: for example if you like running on Saturdays, you may be more likely to befriend people who also enjoy running on Saturdays, and it is not a result of contagion. 

As for the first study, the participants might be more interested in registering to the health website just because the participants are aware that their behavior is monitored in an experiment. 


In [4]:
# read author data from week 2, exercise 2
wd = os.getcwd()
data = wd[:wd.rfind("\\")] + "\\data"
data = data.replace("\\", "/")

part_one = pd.read_csv(f"authorsw1.csv")
#part_two = pd.read_csv(f"{data}/part_two_info_2.csv")
#complete_list = pd.concat([part_one, part_two], ignore_index=True)

final_df = part_one.drop('Unnamed: 0', axis=1)

display(final_df)

id           display_name  \
0     https://openalex.org/A5037267743  Claudia Wagner-Riddle   
1     https://openalex.org/A5031780796          Jonas L. Juul   
2     https://openalex.org/A5055710645          Jon Kleinberg   
3     https://openalex.org/A5056247832              Chloe Ahn   
4     https://openalex.org/A5040523461             Xinyi Wang   
...                                ...                    ...   
1376  https://openalex.org/A5059015114        Coen D. Needell   
1377  https://openalex.org/A5084148692      Elliot E. Pickens   
1378  https://openalex.org/A5054707908       David Rothschild   
1379  https://openalex.org/A5056216760            Anna George   
1380  https://openalex.org/A5004427266           Ana Valdivia   

                                          works_api_url  works_count  h_index  \
0     https://api.openalex.org/works?filter=author.i...          113       37   
1     https://api.openalex.org/works?filter=author.i...           23        5   
2     https://api.openalex.org/works?filter=author.i...          581       97   
3     https://api.openalex.org/works?filter=author.i...            4        1   
4     https://api.openalex.org/works?filter=author.i...         1772       57   
...                                                 ...          ...      ...   
1376  https://api.openalex.org/works?filter=author.i...            3        2   
1377  https://api.openalex.org/works?filter=author.i...            2        1   
1378  https://api.openalex.org/works?filter=author.i...          125       21   
1379  https://api.openalex.org/works?filter=author.i...          149       29   
1380  https://api.openalex.org/works?filter=author.i...           22       10   

     country_code  
0              CA  
1              US  
2              US  
3              US  
4              CN  
...           ...  
1376           US  
1377           GB  
1378           US  
1379           US  
1380           GB  

[1381 rows x 6 columns]

### Filtering/Works Requests


In [5]:
# remove authors with works_count < 5, > 5000
non_contributors = final_df[(final_df.works_count < 5) | (final_df.works_count > 5000)].index
pmos = final_df.drop(non_contributors)
pmos = pmos.reset_index()

In [6]:
# create the request url with the given authors and filters
def build_request(author_ids, cursor="*"):
    auth = "author.id:"
    for id in author_ids:
        auth += f"{id}|"
    auth = auth[:-1]


    concept_filter = "concept.id:https://openalex.org/C17744445|https://openalex.org/C144024400|https://openalex.org/C15744967|https://openalex.org/C162324750,concept.id:https://openalex.org/C121332964|https://openalex.org/C41008148|https://openalex.org/C33923547"
    url = f"https://api.openalex.org/works?per-page=200&cursor={cursor}&filter={auth},{concept_filter},cited_by_count:>10,authors_count:<10"
    return url

In [7]:
# get a list of the authors used in the filter given a start index (max 25)
def get_authors(start):
    query_list = []
    if start + 24 > len(pmos):
        end = len(pmos) - 1
    else:
        end = start + 24
        
    for i in pmos.loc[start:end]["id"]:
        id = i[i.find('A'):]
        query_list.append(id)
    return query_list

In [8]:
# parse the json of a work item in the html response
def get_work_row(item):
    id = item['id']
    pub_year = item['publication_year']
    cite_count = item['cited_by_count']
    authors = [item['authorships'][a]['author'].get('id') for a in range(len(item['authorships']))]
    title = item['title']
    aii = item['abstract_inverted_index']
    
    return [id, pub_year, cite_count, authors, title, aii]

In [9]:
# create empty dataframe to be populated with request data
works_df = pd.DataFrame(columns=['id', 'publication_year', 'cited_by_count', 'author_ids', 'title', 'abstract_inverted_index'])

In [10]:
# fetch the next batch of results using the batch # (counter)
def fetch_results(counter):
    next_cursor = '*'

    while (next_cursor):
        # form request url
        r = build_request(get_authors(counter * 25), next_cursor)
        response = requests.get(r)
        if not response:
            break
        rjson = response.json()

        # set next_cursor for paging
        next_cursor = rjson['meta'].get('next_cursor')
        
        # add results of response to works_df if two two relevant concepts are found 
        for work in rjson['results']:
            work_row = get_work_row(work)
            if work_row[0] not in works_df["id"].values: 
                works_df.loc[len(works_df.index)] = work_row
                       
    

In [13]:
# get the works dataset by fetching all authors
for i in range(45):
    fetch_results(i)

In [15]:
works_df = works_df.drop_duplicates(subset='title').reset_index()
works_df

index                                id  publication_year  \
0         0  https://openalex.org/W2127048411              2010   
1         1  https://openalex.org/W2058105398              2009   
2         2  https://openalex.org/W3142588439              2010   
3         3  https://openalex.org/W2116926372              2012   
4         4  https://openalex.org/W2147453867              2006   
...     ...                               ...               ...   
9346   9470   https://openalex.org/W155200242              2010   
9347   9471   https://openalex.org/W170385551              2010   
9348   9472   https://openalex.org/W105761736              1990   
9349   9473  https://openalex.org/W2003425297              2007   
9350   9474   https://openalex.org/W164174688              2000   

      cited_by_count                                         author_ids  \
0               7467                 [https://openalex.org/A5053938061]   
1               3325  [https://openalex.org/A5031236554, https://ope...   
2               2176  [https://openalex.org/A5017669758, https://ope...   
3               1762  [https://openalex.org/A5017914184, https://ope...   
4               1719  [https://openalex.org/A5058815871, https://ope...   
...              ...                                                ...   
9346              11  [https://openalex.org/A5045037642, https://ope...   
9347              11  [https://openalex.org/A5089575055, https://ope...   
9348              17                 [https://openalex.org/A5045037642]   
9349              12                 [https://openalex.org/A5065243448]   
9350              14  [https://openalex.org/A5015184127, https://ope...   

                                                  title  \
0                         Community detection in graphs   
1                Statistical physics of social dynamics   
2                         Networks, Crowds, and Markets   
3                     Misinformation and Its Correction   
4     Experimental Study of Inequality and Unpredict...   
...                                                 ...   
9346  “You’re as Sick as You Sound”: Using Computati...   
9347  Predicting Human-Targeted Translation Edit Rat...   
9348  Using discourse context to guide pitch accent ...   
9349  Remarks on ghost projections and ideals in the...   
9350  ASR satisficing: the effects of ASR accuracy o...   

                                abstract_inverted_index  
0     {'The': [0], 'modern': [1], 'science': [2], 'o...  
1     {'Statistical': [0], 'physics': [1, 79], 'has'...  
2     {'Are': [0, 30], 'all': [1, 32], 'film': [2], ...  
3     {'The': [0], 'widespread': [1], 'prevalence': ...  
4     {'Hit': [0], 'songs,': [1], 'books,': [2], 'an...  
...                                                 ...  
9346  {'Recently,': [0], 'researchers': [1], 'in': [...  
9347  {'In': [0, 102], 'the': [1, 20, 34, 42, 52, 99...  
9348                                               None  
9349                                               None  
9350  {'We': [0, 26], 'examine': [1], 'how': [2], 'd...  

[9351 rows x 7 columns]

In [17]:
# separate the table into the papers dataset and the abstracts dataset
ic2_papers = works_df[["id", "publication_year", "cited_by_count", "author_ids"]]
ic2_abstracts = works_df[["id", "title", "abstract_inverted_index"]]

In [43]:
# ic2_papers.to_csv("data/papers_dataset.csv")
# ic2_abstracts.to_csv("data/abstracts_dataset.csv")

Data Overview and Reflection questions: 

- Dataset summary: 
    The dataset obtained is including around 9,300 articles.

- Efficiency in code: 
    To make out code more efficient we implemented searching for the authors and articles in batches of 25. In addition, the paging limit was increased from 25 to 200 works per request as suggested in the instructions and we applied the filters directly in the request url.  (The joblib parallel executing was also used to increase efficiency.)

- Filtering Criteria and Dataset Relevance: 
    A primary reason for filtering is to decrease the amount of collected data, and increase efficiency of the code. By filtering on citation count, we compile the most recognized and influential articles to our dataset. By setting specific thresholds for the total number of works by an author we reaffirm that the data collected is the most relevant. With this approach, new authors in the field might be underrepresented in the dataset. The filtering criteria for the concepts on the other hand is necessary to achieve our desired outcome - to collect articles for authors in the field of Computational Social Science. 


### Part 4: The Network of Computational Social Scientists

In [24]:
import networkx as nx
import itertools
from itertools import chain

In [79]:
def create_weighted_egdes(papers): 
    w_edge_list = [] 
    authors_ids = papers["author_ids"].to_list()
    for author_id in authors_ids: 
         # If there are only two authors 
        if len(author_id) == 2 and author_id not in w_edge_list:
            papers_nr = authors_ids.count(author_id)
            w_edge_list.append((author_id[0], author_id[1], papers_nr))

        # if less than two I guess skip? If more than 2 - compute all combinations of authors 
        elif len(author_id) > 2: 
            combinations = list(itertools.combinations(author_id, 2))
            for combination in combinations: 
                papers_nr = authors_ids.count([combination[0], combination[0]])
                w_edge_list.append((combination[0], combination[1], papers_nr))
    return w_edge_list
            
    

In [46]:
def create_nodes(papers):
    auth_exp = papers.explode("author_ids").reset_index(drop=True)
    unique_auths = auth_exp["author_ids"].drop_duplicates()
    first_pub = auth_exp.groupby("author_ids")["publication_year"].min()
    ic2_auths = final_df[["id", "display_name", "country_code"]].merge(first_pub, left_on="id", right_on="author_ids", how="left")
    return ic2_auths

In [47]:
create_nodes(ic2_papers)

id           display_name country_code  \
0     https://openalex.org/A5037267743  Claudia Wagner-Riddle           CA   
1     https://openalex.org/A5031780796          Jonas L. Juul           US   
2     https://openalex.org/A5055710645          Jon Kleinberg           US   
3     https://openalex.org/A5056247832              Chloe Ahn           US   
4     https://openalex.org/A5040523461             Xinyi Wang           CN   
...                                ...                    ...          ...   
1376  https://openalex.org/A5059015114        Coen D. Needell           US   
1377  https://openalex.org/A5084148692      Elliot E. Pickens           GB   
1378  https://openalex.org/A5054707908       David Rothschild           US   
1379  https://openalex.org/A5056216760            Anna George           US   
1380  https://openalex.org/A5004427266           Ana Valdivia           GB   

      publication_year  
0                  NaN  
1               2019.0  
2               1997.0  
3                  NaN  
4               1986.0  
...                ...  
1376               NaN  
1377               NaN  
1378            1942.0  
1379               NaN  
1380               NaN  

[1381 rows x 4 columns]

In [80]:
weighted_egdes = create_weighted_egdes(works_df)

In [ ]:
print((weighted_egdes))

[('https://openalex.org/A5031236554', 'https://openalex.org/A5053938061', 0), ('https://openalex.org/A5031236554', 'https://openalex.org/A5070657345', 0), ('https://openalex.org/A5053938061', 'https://openalex.org/A5070657345', 0), ('https://openalex.org/A5017669758', 'https://openalex.org/A5055710645', 5), ('https://openalex.org/A5017914184', 'https://openalex.org/A5043657584', 0), ('https://openalex.org/A5017914184', 'https://openalex.org/A5047153758', 0), ('https://openalex.org/A5017914184', 'https://openalex.org/A5034259217', 0), ('https://openalex.org/A5017914184', 'https://openalex.org/A5085938112', 0), ('https://openalex.org/A5043657584', 'https://openalex.org/A5047153758', 0), ('https://openalex.org/A5043657584', 'https://openalex.org/A5034259217', 0), ('https://openalex.org/A5043657584', 'https://openalex.org/A5085938112', 0), ('https://openalex.org/A5047153758', 'https://openalex.org/A5034259217', 0), ('https://openalex.org/A5047153758', 'https://openalex.org/A5085938112', 0)

#### 4.2: Preliminary Network Analysis
##### 1. Network Metrics
- Total number of nodes: 14,989
- Total number of links: 64,521         

The maximum possible number of links = (n * (n - 1))/2       with n = 14,989 
- Network density: 64,521/14,989 = 112,327,566
IS IT SPARSE?? ELABORATE <br>

- NETWORK FULLY CONNECTED?? DISCONNECTED?

- Isolated nodes:


- DISCUSS DENSITY/CONNECTIVITY


##### 2. Degree Analysis
- Average:
- Median:
- Mode:
- Minimum degree of nodes:
- Maximum degree of nodes:

##### 3. Top Authors
Top 5 authors:
- 
- 
- 
- 
- 

